# Bewertung Inhaltsbasiertes Empfehlungssystem mit KNN-Klassifikation

## Schritt 1: Einschränken der Daten und Festlegen des Nutzers

Zunächst bestimmen wir den Nutzer, für den unser inhaltsbasiertes Filmempfehlungssystem trainiert werden soll.<br/>
Erinnerung: Inhaltsbasierte Empfehlungssysteme berechnen Empfehlungen in Abhängigkeit der Filminhalte und den Informationen zu einem einzigen Nutzer!

In [2]:
nutzer = 1

## Schritt 2: Datensatzvorbereitung

Wie genau der Datensatz vorbereitet wird findest du in Kapitel 14.5.1.2.

In [3]:
import pandas as pd
import re

ratings = pd.read_csv(r'ratings.csv',encoding='latin-1')
movies = pd.read_csv(r'movies.csv',encoding='latin-1')

movies_filter = movies[movies['movieId']<1000]
for elem in movies_filter['genres'].str.split(pat = '|', expand = False).explode().unique():
    column = []
    for i in range(len(movies_filter)):
        if elem in movies_filter['genres'].str.split(pat = '|', expand = False)[i]:
            column.append(1)
        else:
            column.append(0)
    movies_filter[elem] = column
movies_filter = movies_filter.drop(['title','genres'], axis='columns')

ratings_user = ratings[ratings['userId']==nutzer]
total_user = pd.merge(movies_filter,ratings_user,left_on=['movieId'],
              right_on=['movieId'],
              how='inner').drop(['userId'], axis='columns')
total_user

movieId  Action  Adventure  Sci-Fi  IMAX  Children  Comedy  Fantasy  \
0         4       0          1       0     1         1       1        1   
1         7       0          1       0     0         1       0        0   
2         8       0          0       0     0         0       1        0   
3         9       0          1       0     0         1       1        0   
4        10       1          1       0     0         0       0        1   
5        12       0          1       0     0         1       1        1   
6        14       0          0       0     0         0       1        0   
7        17       0          0       0     0         0       1        0   
8        18       0          1       0     0         1       1        0   
9        22       0          0       0     0         1       1        0   
10       23       0          1       0     1         1       0        0   
11       24       1          1       1     0         0       0        0   
12       27       0          0       0     0         0       0        0   

    Animation  Romance  Drama  War  Crime  Thriller  Musical  rating  
0           0        0      0    0      0         0        0     4.0  
1           0        1      0    0      0         0        0     5.0  
2           0        0      0    0      0         0        0     4.0  
3           1        0      0    0      0         0        0     5.0  
4           0        0      0    0      0         0        0     3.0  
5           1        0      0    0      0         0        0     4.0  
6           0        0      0    0      1         0        0     4.0  
7           0        0      1    0      0         0        0     5.0  
8           1        0      0    0      0         0        0     5.0  
9           0        0      0    0      0         0        0     5.0  
10          1        0      1    0      0         0        1     5.0  
11          0        0      0    0      0         1        0     4.0  
12          0        1      1    0      0         0        0     5.0

## Schritt 3: Klassen und Attribute angeben

Um unser Modell zu trainieren, müssen wir dem Modell sagen, welches die Attribute und welches die Klassen sind, die es vorhersagen soll. Dafür trennen wir den DataFrame in die Attribute, d.h. alle Genre Spalten, und die Klasse, die Spalte ratings.

In [4]:
X = total_user.drop(['rating','movieId'], axis='columns')
y = total_user.rating
X

Action  Adventure  Sci-Fi  IMAX  Children  Comedy  Fantasy  Animation  \
0        0          1       0     1         1       1        1          0   
1        0          1       0     0         1       0        0          0   
2        0          0       0     0         0       1        0          0   
3        0          1       0     0         1       1        0          1   
4        1          1       0     0         0       0        1          0   
5        0          1       0     0         1       1        1          1   
6        0          0       0     0         0       1        0          0   
7        0          0       0     0         0       1        0          0   
8        0          1       0     0         1       1        0          1   
9        0          0       0     0         1       1        0          0   
10       0          1       0     1         1       0        0          1   
11       1          1       1     0         0       0        0          0   
12       0          0       0     0         0       0        0          0   

    Romance  Drama  War  Crime  Thriller  Musical  
0         0      0    0      0         0        0  
1         1      0    0      0         0        0  
2         0      0    0      0         0        0  
3         0      0    0      0         0        0  
4         0      0    0      0         0        0  
5         0      0    0      0         0        0  
6         0      0    0      1         0        0  
7         0      1    0      0         0        0  
8         0      0    0      0         0        0  
9         0      0    0      0         0        0  
10        0      1    0      0         0        1  
11        0      0    0      0         1        0  
12        1      1    0      0         0        0

## Schritt 4: Diskretisieren

Eventuell enthält die Spalte 'ratings' Bewertungen mit halben Sternen, d.h. 3.5 oder 4.5. Du siehst das, wenn du dir y in der vorangegangenen Codezelle ausgeben lässt. Die Funktion der KNN-Klassifikation von python kann nur mit ganzzahligen Klassen arbeiten. Daher müssen wir Einträge der Spalte 'ratings' ganzzahligen Werten zuordnen. Wir können entweder runden, oder eine python-Funktion verwenden, die automatisch ganzzahlige Klassen zuordnet. Im zweiten Fall müssen wir die Vorhersagen wieder zurück interpretieren, also aus den ganzzahligen Klassen wieder die Bewertungen auslesen. Führe die Variante aus, die du nutzen möchtest.

### Achtung: Führe nur eine der beiden Varianten aus!

### Variante: Runden

In [7]:
y_ganzzahlig = y.astype(int)

### Variante: python Funktion

In [5]:
from sklearn import preprocessing
from sklearn import utils

lab = preprocessing.LabelEncoder()
y_transformed = lab.fit_transform(y)
print(y_transformed)
print(y.to_list())

[1 2 1 2 0 1 1 2 2 2 2 1 2]
[4.0, 5.0, 4.0, 5.0, 3.0, 4.0, 4.0, 5.0, 5.0, 5.0, 5.0, 4.0, 5.0]


## Schritt 5: Test-Train-Split

Python bietet eine Funktion, die den Datensatz automatisch in einen Trainings- und Testdatensatz teilt. Diese nutzen wir hier. Mit dem Parameter 'test_size' kannst du die Größe des Testdatensatzes beeinflussen: 0.3 steht für eine Größe von 30% des Gesamtdatensatzes.

In [6]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y_transformed, test_size=0.3, random_state=1)
X_test

Action  Adventure  Sci-Fi  IMAX  Children  Comedy  Fantasy  Animation  \
2        0          0       0     0         0       1        0          0   
3        0          1       0     0         1       1        0          1   
4        1          1       0     0         0       0        1          0   
10       0          1       0     1         1       0        0          1   

    Romance  Drama  War  Crime  Thriller  Musical  
2         0      0    0      0         0        0  
3         0      0    0      0         0        0  
4         0      0    0      0         0        0  
10        0      1    0      0         0        1

## Schritt 6: Modell trainieren

Nun trainieren wir das Modell auf unserem Trainingsdatensatz. Du kannst angeben, wie viele nächste Nachbarn das Modell berücksichtigen soll. Wenn das Modell trainiert ist erhälst du die Ausgabe 'KNeighborsClassifier(n_neighbors=3)'.

In [7]:
from sklearn.neighbors import KNeighborsClassifier
knn = KNeighborsClassifier(n_neighbors=3)
knn.fit(X_train, y_train)

KNeighborsClassifier(n_neighbors=3)

## Schritt 7: Modellevaluierung

Wir berechnen die Vorhersagen für den Testdatensatz.<br/>

In [8]:
y_prognose = knn.predict(X_test)

Beachte dass du die Klassen rückinterpretieren musst, wenn du die echten Bewertungen sehen möchtest und nicht gerundet, sondern die python Funktion verwendet hast. Führe dafür die passende Codezelle aus.

### Variante: Runden

In [ ]:
y_prognose_re = y_prognose
y_test_re = y_test

### Variante: python Funktion

In [11]:
y_prognose_re = lab.inverse_transform(y_prognose)
y_test_re = lab.inverse_transform(y_test)

Hier kannst du dir die echten Klassen und die prognostizierten Klassen anzeigen lassen.

In [12]:
print('Prognostizierte Klassen: ' + str(y_prognose_re))
print('Echte Klassen: ' + str(y_test_re))

Prognostizierte Klassen: [5. 5. 4. 5.]
Echte Klassen: [4. 5. 3. 5.]


### Konfusionsmatrix

In [13]:
from sklearn.metrics import confusion_matrix
confusion_matrix(y_test, y_prognose)

array([[0, 1, 0],
       [0, 0, 1],
       [0, 0, 2]], dtype=int64)

### Mittlere Abweichung der vorhergesagten Bewertungen

In [14]:
from sklearn.metrics import mean_absolute_error
mean_absolute_error(y_test_re,y_prognose_re)

0.5

### Mittlere quadrierte Abweichung der vorhergesagten Bewertungen

In [15]:
from sklearn.metrics import mean_squared_error
mean_squared_error(y_test_re,y_prognose_re)

0.5